In [1]:
import ROOT as R
import array
%jsroot on
import numpy as np


Welcome to JupyROOT 6.16/00


In [2]:
c = R.TCanvas("c")


Definisco qui una funzione da usare dopo:

In [3]:
def rescaleaxis(g,scale=1000/800):
    """This function rescales the x-axis on a TGraph."""
    N = g.GetN()
    x = g.GetX()
    for i in range(N):
        x[i] *= scale
    g.GetHistogram().Delete()
    g.SetHistogram(0)
    return

In [4]:
R.gStyle.SetOptStat(0);

In [5]:
f = R.TFile.Open("./data_out/398/sub_3_G_1.root")

Comincio considerando una GEMROC. Plottiamo le entries vs il tempo (in S)

In [6]:
f.tree.Draw("timestamp>>h(8000,7,9)","","")
c.Draw()

Del buco intorno a 7.85 mi occuperò in seguito.
Zoommando si vedono già delle strutture nel range delle 10/centinaia di Hz
Cominciamo a indagare le strutture a frequenza più bassa (f sample 1kHz). In seguito ho visto che avrei potuto passare direttamente a frequenza più alte, ma così risulta comunque più chairo. Prendo la finestra temporale fra 7.9 e 8.7 e 800 bin. (bin width=1ms, f sample = 1kHz).

In [7]:
n_bins=800
ext_1=7.9
ext_2=8.7

In [8]:
h1= R.TH1F( "h1", 'hit vs time',n_bins , ext_1,ext_2) 

Riempio un istogramma

In [9]:
for  entryNum  in  range(0,f.tree.GetEntries ()):
    f.tree.GetEntry(entryNum)
    timestamp=getattr(f.tree ,"timestamp")
    if timestamp>ext_1 and timestamp<ext_2:
       h1.Fill(timestamp)
h1.SetXTitle("Tempo [s]")
h1.SetYTitle("Entries")

h1.Draw()
c.Draw()

Faccio la trasformata chiedendo il modulo

In [10]:
h_trans=h1.FFT(None,"MAG")

In [11]:
h_trans.Draw()
h_trans.SetTitle("Modulo della FFT")
h_trans.SetXTitle("Bin")

c.Draw()

Passiamo da bin a frequenza. Per farlo sposto i dati in un TGraph, li scalo e li riporto in un istogramma (mi risulta più comodo così che passare da istogramma a istogramma.

In [12]:
gr1=R.TGraph(h_trans) 
rescaleaxis(gr1,1000/800)


In [13]:
h_trans_hz = R.TH1F( "h_trans_hz", 'rate histogram in Hz (not normalized)',n_bins , 0, 1/((ext_2-ext_1)/n_bins)) 

In [14]:
x=array.array('d',[0])
y=array.array('d',[0])


In [15]:
for p in range (0, gr1.GetN()):
    (gr1.GetPoint(p, x, y))
    k = h_trans_hz.FindFixBin(int(x[0]))
    h_trans_hz.SetBinContent(k, int(y[0]))
h_trans_hz.Draw()
h_trans_hz.SetXTitle("Rate [Hz]")
c.Draw()

Estraggo i picchi e li ordino per ampiezza (in realtà non è nemmeno necessario, si vede tutto abbastanza bene comunque). Prendo metà del range per non coffonderci con i simmetrici coniugati.

In [16]:
spect = R.TSpectrum(30)
spect.Search(h_trans_hz)
xs=spect.GetPositionX()
ys=spect.GetPositionY()
peaks=np.zeros((spect.GetNPeaks(),2))
for i in range (0,spect.GetNPeaks()):
    peaks[i]=(xs[i],ys[i])
srted=peaks[np.argsort(peaks[:,1])]
srted=srted[::-1]
for i in range (0,spect.GetNPeaks()):
        if (srted[i,0]<500):
             print (f'Freq {srted[i,0]:.2f},  amplitude {srted[i,1]:.2f}')

Freq 99.38,  amplitude 225838.00
Freq 149.38,  amplitude 47111.00
Freq 440.63,  amplitude 46223.00
Freq 249.38,  amplitude 44523.00
Freq 399.38,  amplitude 41692.00
Freq 299.38,  amplitude 41453.00
Freq 199.38,  amplitude 38951.00
Freq 499.38,  amplitude 34869.00
Freq 49.38,  amplitude 25041.00
Freq 449.38,  amplitude 24537.00


Non saprei bene giudicare questo spetto. Si potrebbe dire che la componente dominante è a 100 hZ (con le relative armoniche), a cui si aggiunge una componente a 50 hZ e armoniche. Non so saprei dire perchè non si vedono componenti a 350 Hz nè perchè 50 Hz e le varie armoniche abbiano tutte ampiezze simili. <br>
Oppure potremmo vederlo com 50 hZ (linea elettrica?) + armoniche e per qualche motivo domina la seconda armonica.

In [17]:
h_trans_hz.GetXaxis().SetRangeUser(0,500)
c.Draw()

Inserisco le funzione fino a qui in uno script e proviamo per diverse frequenze di sampling

In [18]:
import FTT_spectrum as script


Controllo prima di tutto che quanto trovato sopra non fossero costrutti del sampling

In [19]:
h_trans_hz_1=script.extract_spectrum(f.tree,1200,ext_1,ext_2)

Warning in <TFile::Append>: Replacing existing TH1: out_MAG (Potential memory leak).


In [20]:
h_trans_hz_1.Draw()

In [21]:
c.Draw()

Modificando di poco il rate di sampling il risultato non cambia. <br> Passiamo alla regione dei kHz (sampling 10 kHz)

In [22]:
h_trans_hz_2=script.extract_spectrum(f.tree,8000,ext_1,ext_2)
h_trans_hz_2.Draw()
c.Draw()

Warning in <TFile::Append>: Replacing existing TH1: out_MAG (Potential memory leak).
Warning in <TFile::Append>: Replacing existing TH1: h_trasf_hz_2 (Potential memory leak).


Oltre alle strutture viste prima, è comparsa una frequenza molto evidente a 2440 Hz. E' una frequenza che può significare qualcosa? <br>

Passando alla regione delle decine di kHz

In [23]:
h_trans_hz_3=script.extract_spectrum(f.tree,80000,ext_1,ext_2)
h_trans_hz_3.Draw()
c.Draw()

Warning in <TFile::Append>: Replacing existing TH1: out_MAG (Potential memory leak).
Warning in <TFile::Append>: Replacing existing TH1: h_trasf_hz_2 (Potential memory leak).


Le strutture dominanti sembrano quelle trovate prima, compare una serie di picchi a partire da 7325 e un paio di bande intorno ai 24 e 26 kHz

Guardando nelle centinai di kHz

In [24]:
h_trans_hz_3=script.extract_spectrum(f.tree,800000,ext_1,ext_2)
h_trans_hz_3.Draw()
c.Draw()

Warning in <TFile::Append>: Replacing existing TH1: out_MAG (Potential memory leak).
Warning in <TFile::Append>: Replacing existing TH1: h_trasf_hz_2 (Potential memory leak).


Non appaiono strutture significative rispetto a quanto visto prima.

Per guardare ai MHz restringo, di molto, l'intervallo utilizzato per avere tempi di computazione accettabili:

In [27]:
h_trans_hz_4=script.extract_spectrum(f.tree,100000,8,8.01)
h_trans_hz_4.Draw()
c.Draw()

Warning in <TFile::Append>: Replacing existing TH1: out_MAG (Potential memory leak).
Warning in <TFile::Append>: Replacing existing TH1: h_trasf_hz_2 (Potential memory leak).
